In [1]:
import graphlab

In [2]:
data = graphlab.SFrame('kc_house_data.gl/')

This non-commercial license of GraphLab Create for academic use is assigned to amandalmia18@gmail.com and will expire on August 21, 2017.


[INFO] graphlab.cython.cy_server: GraphLab Create v2.1 started. Logging: /tmp/graphlab_server_1474924321.log


In [3]:
import numpy as np

In [7]:
def get_numpy_data(data_sframe,features,output):
    data_sframe['constant']=1
    features=['constant']+features
    features_sframe=data_sframe.select_columns(features)
    features_matrix = features_sframe.to_numpy()
    output_sarray = data_sframe[output]
    output_array = output_sarray.to_numpy()
    return(features_matrix,output_array)

In [9]:
def predict_outcome(feature_matrix,weights):
    predictions = np.dot(feature_matrix,weights)
    return predictions

In [10]:
train_data,test_data=data.random_split(.8, seed=0)

In [13]:
simple_features=['sqft_living']
my_output='price'
(simple_feature_matrix,output)=get_numpy_data(train_data,simple_features,my_output)

In [18]:
output

array([ 221900.,  538000.,  180000., ...,  360000.,  400000.,  325000.])

In [16]:
train_data['sqft_living']

dtype: float
Rows: 17384
[1180.0, 2570.0, 770.0, 1960.0, 1680.0, 5420.0, 1715.0, 1060.0, 1780.0, 1890.0, 3560.0, 1160.0, 1370.0, 1810.0, 1890.0, 1600.0, 1200.0, 1250.0, 1620.0, 3050.0, 2270.0, 1070.0, 2450.0, 2450.0, 1400.0, 1520.0, 2570.0, 1190.0, 2330.0, 2060.0, 2300.0, 1660.0, 2360.0, 1220.0, 2570.0, 3595.0, 1570.0, 1280.0, 3160.0, 990.0, 2290.0, 1250.0, 2753.0, 1190.0, 3150.0, 1410.0, 1980.0, 2730.0, 2830.0, 2420.0, 3250.0, 1850.0, 2150.0, 2519.0, 1540.0, 1660.0, 2770.0, 2720.0, 2240.0, 1000.0, 3200.0, 4770.0, 1260.0, 2380.0, 3430.0, 1760.0, 1040.0, 1410.0, 3450.0, 2350.0, 2020.0, 1680.0, 960.0, 2140.0, 2660.0, 2770.0, 1610.0, 1030.0, 3520.0, 1200.0, 1580.0, 1580.0, 3300.0, 1160.0, 1810.0, 2320.0, 2070.0, 1980.0, 2190.0, 2920.0, 1210.0, 2340.0, 1670.0, 1240.0, 3140.0, 2310.0, 1260.0, 1540.0, 2080.0, 4380.0, ... ]

In [19]:
def feature_derivative(errors,feature):
    dotP = np.dot(errors,feature)
    derivative = dotP*2
    return derivative

In [21]:
initial_weights=np.array([-47000., 1.])
step_size=7e-12
tolerance=2.5e7

In [44]:
predictions = predict_outcome(simple_feature_matrix,initial_weights)
errors = predictions-output
derivative=feature_derivative(errors,simple_feature_matrix[:,1])
initial_weights[1] -= step_size*derivative
print derivative*derivative

1.16212159974e+25


In [55]:
import math
def regression_gradient_descent(feature_matrix,output,initial_weights,step_size,tolerance):
    converged=False
    weights=np.array(initial_weights)
    while not converged:
        
        predictions = predict_outcome(feature_matrix,weights)
        errors=predictions-output
        
        gradient_sum_squares = 0
        for i in range(len(weights)):
            derivative = feature_derivative(errors,feature_matrix[:,i])
            gradient_sum_squares += derivative*derivative
            weights[i] -= step_size*derivative
        
        gradient_magnitude = math.sqrt(gradient_sum_squares)
        if gradient_magnitude < tolerance:
            converged=True
    
    return weights

In [56]:
simple_weights = regression_gradient_descent(simple_feature_matrix, output, initial_weights,step_size, tolerance)

In [57]:
simple_feature_matrix

array([[  1.00000000e+00,   1.18000000e+03],
       [  1.00000000e+00,   2.57000000e+03],
       [  1.00000000e+00,   7.70000000e+02],
       ..., 
       [  1.00000000e+00,   1.53000000e+03],
       [  1.00000000e+00,   1.60000000e+03],
       [  1.00000000e+00,   1.02000000e+03]])

In [58]:
simple_weights

array([-47000.00201867,    281.91216527])

In [59]:
(test_simple_feature_matrix,test_output) = get_numpy_data(test_data,simple_features,my_output)

In [96]:
test_output

array([ 310000.,  650000.,  233000., ...,  610685.,  400000.,  402101.])

In [61]:
test_simple_weights = regression_gradient_descent(test_simple_feature_matrix,test_output,initial_weights,step_size,tolerance)

In [97]:
predictions = predict_outcome(test_simple_feature_matrix,simple_weights)

In [98]:
predictions

array([ 356134.394321  ,  784640.8855352 ,  435069.8005973 , ...,
        663418.65446802,  604217.0997608 ,  240550.40655928])

In [65]:
test_data[0]['price']

310000.0

In [66]:
def get_residual_sum_of_squares(feature_matrix, weights,outcome):
    predictions = predict_outcome(feature_matrix,weights)
    residue = outcome - predictions
    RSS = residue*residue
    return sum(RSS)


In [76]:
print get_residual_sum_of_squares(test_simple_feature_matrix,test_simple_weights,np.array(test_data['price']))

2.75395696884e+14


In [68]:
predictions

array([ 356774.21396264,  785960.7870729 ,  435834.89848295, ...,
        664546.16441671,  605250.65102648,  241006.7830579 ])

In [69]:
test_data['price']

dtype: float
Rows: 4229
[310000.0, 650000.0, 233000.0, 580500.0, 535000.0, 605000.0, 775000.0, 292500.0, 289000.0, 571000.0, 349000.0, 360000.0, 243500.0, 247500.0, 470000.0, 480000.0, 770000.0, 519950.0, 527700.0, 420000.0, 890000.0, 282950.0, 255000.0, 420000.0, 807100.0, 284000.0, 917500.0, 425000.0, 260000.0, 297000.0, 274250.0, 840000.0, 677900.0, 280000.0, 279950.0, 479950.0, 264950.0, 1025000.0, 2400000.0, 260000.0, 525000.0, 369900.0, 210000.0, 304900.0, 170000.0, 2050000.0, 780000.0, 330000.0, 360000.0, 550000.0, 208633.0, 315000.0, 1384000.0, 1400000.0, 548000.0, 520000.0, 230000.0, 232000.0, 740000.0, 640000.0, 940000.0, 559900.0, 265000.0, 425000.0, 552250.0, 206600.0, 299000.0, 855000.0, 437500.0, 420000.0, 795000.0, 810000.0, 338000.0, 315000.0, 450000.0, 799000.0, 403950.0, 490000.0, 330000.0, 927000.0, 530000.0, 352000.0, 322500.0, 650000.0, 339000.0, 570000.0, 423000.0, 482000.0, 1300000.0, 988000.0, 1000000.0, 350000.0, 205000.0, 333500.0, 255000.0, 348000.0, 325000.0

In [70]:
test_data['price']-predictions

dtype: array
Rows: 4229
[array('d', [-46774.21396264032, -475960.78707290045, -125834.8984829514, -298074.2469022005, 49228.045812023105, -382782.12317396246, -834557.4632900257, -278309.07577212283, 1226.9159246913623, -419488.86955839256, -148423.66548875457, -179483.22012173396, -202071.98712753714, -196424.79537608626, -216189.96650616406, -555021.4715932115, -464666.4035699989, 26639.278806219925, -439254.04068847036, 57698.83343919931, -363016.95204388467, 4050.5118004168035, -224660.75413334032, -213366.37063043867, -399723.69842831476, -83480.96034707048, -738555.2035153622, 40757.258184846956, -114540.51498004986, -190777.6036246355, 100052.77157508023, -343251.78091380687, -331957.39741090534, 116994.34682943262, -137129.28198585298, -69362.9809684435, -128658.49435867683, -704672.0530066576, -673612.4983736782, -154070.8572402054, -235955.13763624185, 142406.70971096118, -123011.30260722601, -377134.9314225116, 114170.7509537072, -724437.2241367353, -631258.5602377972, -3263

In [73]:
outcome = np.array(test_data['price'])

In [74]:
outcome

array([ 310000.,  650000.,  233000., ...,  610685.,  400000.,  402101.])

In [75]:
print outcome-predictions

[ -46774.21396264 -135960.7870729  -202834.89848295 ...,  -53861.16441671
 -205250.65102648  161094.2169421 ]


In [88]:
model_features = ['sqft_living', 'sqft_living15']
my_output = 'price'
(test_feature_matrix, test_output) = get_numpy_data(test_data, model_features,my_output)
initial_weights = np.array([-100000., 1., 1.])
step_size = 4e-12
tolerance = 1e9

In [78]:
weights = regression_gradient_descent(feature_matrix,output,initial_weights,step_size,tolerance)

In [91]:
test_feature_matrix

array([[  1.00000000e+00,   1.43000000e+03,   1.78000000e+03],
       [  1.00000000e+00,   2.95000000e+03,   2.14000000e+03],
       [  1.00000000e+00,   1.71000000e+03,   1.03000000e+03],
       ..., 
       [  1.00000000e+00,   2.52000000e+03,   2.52000000e+03],
       [  1.00000000e+00,   2.31000000e+03,   1.83000000e+03],
       [  1.00000000e+00,   1.02000000e+03,   1.02000000e+03]])

In [92]:
print predict_outcome(test_feature_matrix,weights)

[ 366651.41203656  762662.39786164  386312.09499712 ...,  682087.39928241
  585579.27865729  216559.20396617]


In [93]:
predict_outcome(test_feature_matrix,weights)- np.array(test_data['price'])

array([  56651.41203656,  112662.39786164,  153312.09499712, ...,
         71402.39928241,  185579.27865729, -185541.79603383])

In [95]:
print get_residual_sum_of_squares(test_feature_matrix,weights, np.array(test_data['price']))

2.70263446465e+14
